In [1]:
import h5py
import numpy as np
import healpy as hp
import ipyvolume as ipv

In [2]:
sim = h5py.File('/data/cielo/simulations/LG1/LG1.hdf5', 'r')
Bhdata = h5py.File('BetterVectorList_V2.h5', 'r')

In [3]:
satList = Bhdata['SatelliteList'][()]
cenList = Bhdata['SatelliteCentral'][()]
maxVect = Bhdata['BetterVectors'][()]
deltaSFR = Bhdata['MaxDeltaSFR'][()]

In [4]:
def plot3D_BH(fofID, central, maxVect):
    nside = 8
    npix = hp.nside2npix(nside)
    
    OffSets = sim['SnapNumber_128/SubGroups/PartType0/Offsets'][fofID].astype('int')
    starOff = sim['SnapNumber_128/SubGroups/PartType4/Offsets'][fofID].astype('int')
    
    PosGas = sim['SnapNumber_128/PartType0/Coordinates'][OffSets[0]:OffSets[1]]
    SFRGas = sim['SnapNumber_128/PartType0/StarFormationRate'][OffSets[0]:OffSets[1]]
    MassGas = sim['SnapNumber_128/PartType0/Masses'][OffSets[0]:OffSets[1]]
    
    PosStar = sim['SnapNumber_128/PartType4/Coordinates'][starOff[0]:starOff[1]]
    
    velGal = sim['SnapNumber_128/SubGroups/SubGroupVel'][fofID]
    velCen = sim['SnapNumber_128/SubGroups/SubGroupVel'][central]
    
    deltaVel = velGal - velCen
    
    cen = sim['SnapNumber_128/SubGroups/SubGroupPos'][fofID]
    cen1 = sim['SnapNumber_128/SubGroups/SubGroupPos'][central]
    
    x, y, z = PosGas[:,0]-cen[0], PosGas[:,1]-cen[1], PosGas[:,2]-cen[2]
    xS, yS, zS = PosStar[:,0]-cen[0], PosStar[:,1]-cen[1], PosStar[:,2]-cen[2]
    
    pix = hp.pixelfunc.vec2pix(nside, x, y, z)
    
    ind0 = hp.query_disc(nside, maxVect, np.pi/2.)
    
    index_bool = np.in1d(pix, ind0)
    index_onehalf = np.where(index_bool)[0]
    index_otherhalf = np.where(index_bool==False)[0]
    
    xone, yone, zone = x[index_onehalf], y[index_onehalf], z[index_onehalf]
    xother, yother, zother = x[index_otherhalf], y[index_otherhalf], z[index_otherhalf]

    xcen, ycen, zcen = np.array([cen1[0] - cen[0]]), np.array([cen1[1] - cen[1]]), np.array([cen1[2] - cen[2]])
    
    print('blue:\tthe better half\nred:\tthe worst(?) half')
    
    fig = ipv.figure(width=750, height=750)

    scatter1 = ipv.scatter(xone, yone, zone, marker='sphere', size=.5, color='blue')
    scatter2 = ipv.scatter(xother, yother, zother, marker='sphere', size=.5, color='red')
   
    stars = ipv.scatter(xS, yS, zS, marker='sphere', size=.25, color='grey')
#     centre = ipv.scatter(xcen, ycen, zcen, marker='sphere', size=.5, color='black')
    
    zero = np.array([0.])
    vx, vy, vz = np.array([deltaVel[0]]), np.array([deltaVel[1]]), np.array([deltaVel[2]])
    
    quiv = ipv.quiver(zero, zero, zero, vx, vy, vz, color='black')
    centre = ipv.quiver(zero, zero, zero, xcen, ycen, zcen, color='orange')
      
    ipv.show()

In [5]:
ii = np.argsort(deltaSFR)
iilow = ii[:3]
iihigh = ii[-3:]

In [6]:
for ss, cc, mV in zip(satList[iilow], cenList[iilow], maxVect[iilow]):
    print('SubGroup {}\n'.format(ss))
    
    plot3D_BH(ss, cc, mV)

SubGroup 2178

blue:	the better half
red:	the worst(?) half


SubGroup 2101

blue:	the better half
red:	the worst(?) half


SubGroup 152

blue:	the better half
red:	the worst(?) half


In [7]:
for ss, cc, mV in zip(satList[iihigh], cenList[iihigh], maxVect[iihigh]):
    print('SubGroup {}\n'.format(ss))
    
    plot3D_BH(ss, cc, mV)

SubGroup 4474

blue:	the better half
red:	the worst(?) half


SubGroup 82

blue:	the better half
red:	the worst(?) half


SubGroup 2099

blue:	the better half
red:	the worst(?) half
